In [10]:
from teste import EmissionLines
import plotly.express as px
import plotly.graph_objects as go
import pandas as pd

filepath='images/manga-9894-3701-MEGACUBE.fits' 
x=20
y=25

my_cube = EmissionLines(filepath)
obs_synt = my_cube.obs_and_synt_spec(x, y)
em_lines = my_cube.emission_lines_profile(x, y)
print(em_lines)


[{'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'hb'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'o3_4959'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'o3_5007'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'He1_5876'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'o1_6300'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-17]), 'label': 'n2_6548'}, {'data': array([1.23925042e-17, 1.21060227e-17, 1.17460581e-17, ...,
       2.36602672e-17, 2.37108024e-17, 2.37444977e-1

In [11]:
df1 = pd.DataFrame(dict(
        wavelength=my_cube.wavelength,
        flux=obs_synt['flux']['data'],
        synt=obs_synt['synt']['data']))

for line in em_lines:
    df1[line['label']] = line['data']
df1.head()

v_abs_lines = my_cube.absortion_lines()
v_em_lines = my_cube.emission_lines(x, y)

In [12]:

import plotly as pl

# fig = px.line(df1, x="wavelength", y=["flux", "synt"])

fig = go.Figure()

fig.add_trace(go.Scatter(
    x=df1["wavelength"],
    y=df1["flux"],
    name="Obs. Spec",
    mode="lines",
    line=dict(color="blue"),
    showlegend=True,
))

fig.add_trace(go.Scatter(
    x=df1["wavelength"],
    y=df1["synt"],
    name="Synt. Spec",
    mode="lines",
    line=dict(color="orange"),
    showlegend=True,
))

show_legend = True
for line in em_lines:
    label = line['label']

    fig.add_trace(go.Scatter(
        x=df1["wavelength"],
        y=df1[label],
        legendgroup="em_lines",
        name="Emission-lines",
        mode="lines",
        line=dict(color="black", dash='dot'),
        showlegend=show_legend,
    ))
    show_legend = False

for line in v_abs_lines:
    fig.add_vline(x=line['value'], line_dash="dash", line_color="green", annotation_text=line["label"], annotation_position="bottom right")

for line in v_em_lines:
    fig.add_vline(x=line['value'], line_dash="dash", line_color="cyan", annotation_text=line["label"], annotation_textangle=-90)

# fig.add_trace(go.Scatter(
#     x=df1["wavelength"],
#     y=df1["o3_4959"],
#     legendgroup="group",
#     # name="first legend group - average",
#     mode="lines",
#     showlegend=False,
# ))

# for line in em_lines:
# fig.add_trace(y="hb")
# fig.add_trace(y="o3_4959")
fig.show()
fig.write_html("exemplo_plotly.html")

In [28]:
from teste import EmissionLines
import plotly as pl
import plotly.express as px
import plotly.graph_objects as go

filepath='images/manga-9894-3701-MEGACUBE.fits' 
x=20
y=25
my_cube = EmissionLines(filepath)
df = my_cube.to_dataframe(x, y)
em_lines = my_cube.emission_lines(x, y)
abs_lines = my_cube.absortion_lines()
# print(df.head())

fig = go.Figure()
fig.update_layout(
    title=dict(
        text="Spectrum",
        # xanchor="center",
        # yanchor="top"
    ),
    xaxis_title="Wavelength ($\AA$)",
    yaxis_title="Spectral flux density",
    legend=dict(
        title_font_family='Courier New',
        font=dict(
            size=8
        )
    )
    # legend=dict(
    #     orientation="h",
    #     yanchor="bottom",
    #     y=1.02,
    #     xanchor="right",
    #     x=1
    # )
)

fig.add_trace(go.Scatter(
    x=df["wavelength"],
    y=df["obs_spec"],
    name="Obs. Spec",
    mode="lines",
    line=dict(color="blue"),
    showlegend=True,
))

fig.add_trace(go.Scatter(
    x=df["wavelength"],
    y=df["synt_spec"],
    name="Synt. Spec",
    mode="lines",
    line=dict(color="orange"),
    showlegend=True,
))

show_legend = True
for label in df.columns:
    if label in ["wavelength", "obs_spec", "synt_spec"]:
        continue

    fig.add_trace(go.Scatter(
        x=df["wavelength"],
        y=df[label],
        legendgroup="em_lines",
        name="Emission-lines",
        mode="lines",
        line=dict(color="black", dash='dot'),
        showlegend=show_legend,
    ))
    show_legend = False

plot_y_min = fig.data[0].y.min()
plot_y_max = fig.data[0].y.max()
show_legend = True
for line in em_lines:
    fig.add_trace(go.Scatter(
        x=[line['value'],line['value']],
        y=[plot_y_min, plot_y_max],
        legendgroup="v_em_lines",
        name="Em. Lines",
        mode="lines",
        line=dict(color="green", dash='dash'),
        showlegend=show_legend
    ))
    show_legend = False

plot_y_min = fig.data[0].y.min()
plot_y_max = fig.data[0].y.max()
show_legend = True
for line in abs_lines:
    fig.add_trace(go.Scatter(
        x=[line['value'],line['value']],
        y=[plot_y_min, plot_y_max],
        legendgroup="v_abs_lines",
        name="Abs. Lines",
        mode="lines",
        line=dict(color="cyan", dash='dash'),
        showlegend=show_legend
    ))
    show_legend = False


fig.show()
